In [ ]:
import gym
import mujoco_py
import numpy as np

# set PATH=C:\Users\sas02\.mujoco\mujoco200\bin;%PATH%

env = gym.make('FetchSlide-v1')
obs = env.reset()
done = False

def policy(observation, desired_goal):
    # Here you would implement your smarter policy. In this case,
    # we just sample random actions.
    return env.action_space.sample()

while not done:
    action = policy(obs['observation'], obs['desired_goal'])
    obs, reward, done, info = env.step(action)
    env.render()

    # If we want, we can substitute a goal here and re-compute
    # the reward. For instance, we can just pretend that the desired
    # goal was what we achieved all along.
    substitute_goal = obs['achieved_goal'].copy()
    substitute_reward = env.compute_reward(
        obs['achieved_goal'], substitute_goal, info)
    print(f'reward is {reward}, substitute_reward is {substitute_reward}')

In [ ]:
import gym
import mujoco_py
import numpy as np

env = gym.make('FetchSlide-v1')
obs = env.reset()
done = False

action = env.action_space.sample()

obs, reward, done, info = env.step(action)

print(obs, reward, done, info)

In [39]:
import gym
import itertools
import mujoco_py
import numpy as np
import random
import pandas as pd

env = gym.make('FetchSlide-v1', reward_type='dense')

NUM_EPOCH = 10
EPOCH_SIZE = 50
T = 50
GOALS = 5
BATCHES = 40
BATCH_SIZE = 256
NOISE_SCALE = .2
epsilon = .3

# Change to normal distribution across action space
actions =  np.linspace(-1, 1, 10)
actions = list(itertools.permutations(actions, 4))

# weights = np.loadtxt('weights.txt')
weights = np.random.random_sample(35)
targets = weights

policy_func = np.random.random_sample(31 * 4).reshape(4, 31)
policy_targ = policy_func

for epoch in range(NUM_EPOCH):
    
    observations = list()
    rewards = np.array([])
    replay_buffer = list()
    
    for episode in range(EPOCH_SIZE):


        observation = env.reset()

        # goal = observation['desired_goal']
        # state = observation['observation']
        # position = observation['achieved_goal']    

        for t in range(T):
            # env.render() 
            noise = np.random.rand(4) * NOISE_SCALE
            action = policy_ddpg(observation, noise, actions, policy_func)
            
            assert not np.isnan(np.sum(action)), f'Action invalid: {action}'

            new_observation, reward, done, info = env.step(action)
            observations.append((observation, action, new_observation, done))

            observation = new_observation

            if done:
                # print("Episode finished after {} timesteps".format(t+1))
                break

        for state, action, new_state, done in observations:
            rewards = np.append(rewards, env.compute_reward(new_state['achieved_goal'], state['desired_goal'], ''))

            replay_buffer.append((state, action, new_state, rewards[-1], done))

            for g in range(GOALS):
                
                if np.random.rand() >= .8:
                    continue
                
                goal = np.random.uniform(-.3, .3, size=3)
                goal += np.array([.4, 0, 0])

                r = env.compute_reward(state['achieved_goal'], goal, '')

                old_state = observations[t][0]
                old_state['desired_goal'] = goal

                new_state = observations[t][2]
                new_state['desired_goal'] = goal

                replay_buffer.append((old_state, action, new_state, r, done))

        for n in range(BATCHES):
            batch = random.choices(replay_buffer, k=BATCH_SIZE)
            train_ddpg(batch, actions, weights, targets, policy_func, policy_targ)


        print(f'Episode {episode + EPOCH_SIZE * epoch} Complete, Average Return: {rewards.mean()}')
        
        
print(f'Final Weights: {weights}')
np.savetxt('weights.txt', weights)



Episode 0 Complete, Average Return: -0.10623139874646974
Episode 1 Complete, Average Return: -0.21725471869267243
Episode 2 Complete, Average Return: -0.29096099832059025
Episode 3 Complete, Average Return: -0.3252755137979159
Episode 4 Complete, Average Return: -0.3356426758570869
Episode 5 Complete, Average Return: -0.35908311344643523
Episode 6 Complete, Average Return: -0.3701676968136817
Episode 7 Complete, Average Return: -0.38856397895787104
Episode 8 Complete, Average Return: -0.40742287389621396
Episode 9 Complete, Average Return: -0.42119711825269035
Episode 10 Complete, Average Return: -0.42714329874360063
Episode 11 Complete, Average Return: -0.4306806951675423
Episode 12 Complete, Average Return: -0.4307463777814387
Episode 13 Complete, Average Return: -0.4294729714923601
Episode 14 Complete, Average Return: -0.4286483912051352
Episode 15 Complete, Average Return: -0.42921918082568095
Episode 16 Complete, Average Return: -0.4290902245702257
Episode 17 Complete, Average Ret

D:\Anaconda3\lib\site-packages\ipykernel_launcher.py:84: RuntimeWarning: overflow encountered in double_scalars
D:\Anaconda3\lib\site-packages\ipykernel_launcher.py:88: RuntimeWarning: invalid value encountered in double_scalars
D:\Anaconda3\lib\site-packages\ipykernel_launcher.py:63: RuntimeWarning: invalid value encountered in double_scalars


[-inf -inf -inf -inf -inf -inf -inf -inf  inf  nan  nan  inf -inf  inf
 -inf -inf -inf -inf  inf  inf  inf  inf  inf -inf -inf -inf -inf -inf
 -inf -inf -inf -inf -inf -inf -inf]
[0.8774197216083707, 0.5915292195289922, 0.4191210816558439, 0.910494226759566, 0.8125188098667216, 0.4140153165751568, 0.033074505151195366, 0.22098959033772947, -0.005105765080687108, 0.0, 0.0, -0.005306992799109051, 0.0005440898977337245, -0.1427930327872809, 0.012310999517783102, 0.016199622370838444, 0.0005905867849173945, 0.018343329648036543, -0.0034587155524409196, -0.020232194635803426, -0.012353631727202129, -0.016207161487366145, -0.0005183840170971527, 0.016485401173820514, 0.00032726523312605316, 1.0, 1.0, 1.0, 1.0, 0.910494226759566, 0.8125188098667216, 0.4140153165751568, 1.6145057681764738, 0.749150210728291, 0.4140189435205262]
[-inf -inf -inf -inf -inf -inf -inf -inf  inf  nan  nan  inf -inf  inf
 -inf -inf -inf -inf  inf  inf  inf  inf  inf -inf -inf -inf -inf -inf
 -inf -inf -inf -inf -inf 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




[0.9007767951925414, 1.2363714644012735, 0.8553012437620645, 1.0808938632752076, 0.8252380838256028, 0.41401832849210163, 0.18011706808266625, -0.4111333805756707, -0.4412829152699629, 0.0, 0.0, 0.005266358626489192, -0.0004766842309440026, -0.9246773344435085, 0.0009287320200976073, -0.0007887613319537145, -0.0003388267031503944, -0.018415576762514502, 0.003342358275785256, -0.01929353408197637, -0.0009709379030604378, 0.0007798952340111722, 0.0004105950930148604, 5.023749654373358e-07, 0.00014856481988898468, nan, nan, nan, nan, 1.0808938632752076, 0.8252380838256028, 0.41401832849210163, 0.4478586618928854, 0.2194272050599953, 0.2923680854346337]
[nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan]
[0.9007767951925414, 1.2363714644012735, 0.8553012437620645, 1.0808938632752076, 0.8252380838256028, 0.41401832849210163, 0.18011706808266625, -0.4111333805756707, -0.4412829152699629, 0.0, 0.0, 0.0

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




[0.9007767951925414, 1.2363714644012735, 0.8553012437620645, 1.0808938632752076, 0.8252380838256028, 0.41401832849210163, 0.18011706808266625, -0.4111333805756707, -0.4412829152699629, 0.0, 0.0, 0.005266358626489192, -0.0004766842309440026, -0.9246773344435085, 0.0009287320200976073, -0.0007887613319537145, -0.0003388267031503944, -0.018415576762514502, 0.003342358275785256, -0.01929353408197637, -0.0009709379030604378, 0.0007798952340111722, 0.0004105950930148604, 5.023749654373358e-07, 0.00014856481988898468, nan, nan, nan, nan, 1.0808938632752076, 0.8252380838256028, 0.41401832849210163, 0.4478586618928854, 0.2194272050599953, 0.2923680854346337]
[nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan]
[0.9007767951925414, 1.2363714644012735, 0.8553012437620645, 1.0808938632752076, 0.8252380838256028, 0.41401832849210163, 0.18011706808266625, -0.4111333805756707, -0.4412829152699629, 0.0, 0.0, 0.0

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




[0.9007767951925414, 1.2363714644012735, 0.8553012437620645, 1.0808938632752076, 0.8252380838256028, 0.41401832849210163, 0.18011706808266625, -0.4111333805756707, -0.4412829152699629, 0.0, 0.0, 0.005266358626489192, -0.0004766842309440026, -0.9246773344435085, 0.0009287320200976073, -0.0007887613319537145, -0.0003388267031503944, -0.018415576762514502, 0.003342358275785256, -0.01929353408197637, -0.0009709379030604378, 0.0007798952340111722, 0.0004105950930148604, 5.023749654373358e-07, 0.00014856481988898468, nan, nan, nan, nan, 1.0808938632752076, 0.8252380838256028, 0.41401832849210163, 0.4478586618928854, 0.2194272050599953, 0.2923680854346337]
[nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan]
[0.9007767951925414, 1.2363714644012735, 0.8553012437620645, 1.0808938632752076, 0.8252380838256028, 0.41401832849210163, 0.18011706808266625, -0.4111333805756707, -0.4412829152699629, 0.0, 0.0, 0.0

AssertionError: Action invalid: [nan nan nan nan]

In [36]:
def policy(observation, epsilon, actions, weights):
    """ Using e-greedy scheduling, gives an action from the list of possible actions
    
    Args:
        
        observation : The current state
        epsilon : The current epsilon value
        actions : A list of discretized actions that can be made
        
    Returns:
         action : An action for the robot to apply
    """
    
    # length = sum(1 for ignore in actions)
    
    if np.random.rand() < epsilon:
        return random.choice(actions)
    
    best = float('-inf')
    best_action = None
        
    for action in actions:
        q = q_value(observation['observation'], action, observation['achieved_goal'], observation['desired_goal'], weights)
        assert(q > float('-inf'))
            
        if q > best:
            best = q
            best_action = action
            
                
    return np.clip(best_action + noise, -1, 1)
    
    
def train(batch, actions, weights, targets=None):
    
    LEARNING_RATE = .1
    STEP_DECREASE = .9
    
    for state, curr_action, new_state, reward, done in batch:
        
        best = float('-inf')
        best_action = None
        
        for action in actions:
            q = q_value(state['observation'], action, state['achieved_goal'], state['desired_goal'], weights)
            
            if q > best: 
                best = q
                best_action = action
                
        q = q_value(state['observation'], action, state['achieved_goal'], state['desired_goal'], weights)        
        
        difference = (reward + STEP_DECREASE * best) - q
        features = [e for l in np.array([state['observation'], action, state['achieved_goal'], state['desired_goal']]) for e in l]
        weights = weights + [LEARNING_RATE * difference * feature for feature in features] 

    # print(f'Completed a round of training, our new weights are: {weights}\n')
    
def q_value(state, action, position, goal, weights):
    
    features = [e for l in np.array([state, action, position, goal]) for e in l]
    
    total = sum(weights * features)    
    
    if np.isnan(total):
        print(weights)
        print(features)
        
    return total

def train_ddpg(batch, actions, weights, targets, policy_func, policy_targ):
    
    LEARNING_RATE = .1
    STEP_DECREASE = .9
    P = .95
    
    l = 0
    
    for state, curr_action, new_state, reward, done in batch:
        action = policy_ddpg(state, 0, actions, policy_targ)
        
        y = reward + STEP_DECREASE * (1 - done) * q_value(state['observation'], action, state['achieved_goal'], state['desired_goal'], targets)
        
        l = 2 * (y - q_value(state['observation'], curr_action, state['achieved_goal'], state['desired_goal'], weights))
    
        features = [e for lis in np.array([state['observation'], action, state['achieved_goal'], state['desired_goal']]) for e in lis]
        
        weights += [LEARNING_RATE * l * (1 / len(batch)) * feature for feature in features]
        
        action = policy_ddpg(state, 0, actions, policy_func)
        q = q_value(state['observation'], action, state['achieved_goal'], state['desired_goal'], weights)
        features = [e for lis in np.array([state['observation'], state['achieved_goal'], state['desired_goal']]) for e in lis]
        policy_func += [LEARNING_RATE * q * (1 / len(batch)) * feature for feature in features]
        
    targets = P * targets + (1 - P) * weights
    policy_targ = P * policy_targ + (1 - P) * policy_func
    
def policy_ddpg(state, noise, actions, policy_func):
    keys = ['observation', 'achieved_goal', 'desired_goal']
    
    features = np.array([])
    
    for k in keys:
        features = np.append(features, observation[k])

    features = np.tile(features, (4, 1))
    
    proposed_action = np.zeros(4) 
    
    for i in range(4):
        proposed_action[i] = sum(features[i, :] * policy_func[i, :])
            
        
    return np.clip(proposed_action + noise, -1, 1)

In [ ]:
test = list()

test.append((1, 2))
test.append((3, 4))

test

In [ ]:
import gym
import itertools
import mujoco_py
import numpy as np
import random
import pandas as pd

np.savetxt('weights.txt', old_weights)

env = gym.make('FetchSlide-v1', reward_type='dense')

observation = env.reset()

env.observation_space